# Categorizing urban density

last modified: July, 2017

author: [Raj Singh](https://developer.ibm.com/clouddataservices/author/rrsingh/)

original: https://github.com/ibm-cds-labs/open-data/blob/master/samples/urbanity.ipynb


## Overview

Exploration of an academic study of urban structure and density described in the June 2014 article, ["From Jurisdictional to Functional Analysis of Urban Cores & Suburbs"](http://www.newgeography.com/content/004349-from-jurisdictional-functional-analysis-urban-cores-suburbs) in [new geography](http://www.newgeography.com/). 

## Categories

- Urban (pre-auto urban core): density > 2,900 sq. km
- Auto suburban, early: median house built 1946 to 1979, density < 2,900 sq. km and density > 100 sq. km
- Auto suburban, later: median house built after 1979, density < 2,900 sq. km and density > 100 sq. km
- Auto exurban: all others


In [1]:
import pandas as pd, numpy as np, os

## Collect U.S. Census data

Census data from the 2013 US Census American Community Survey (ACS), 5-year estimates.

Created from the "zip code tabulation area" (ZCTA) [TIGER/Line® with Selected Demographic and Economic Data product in Geodatabase format](http://www.census.gov/geo/maps-data/data/tiger-data.html). This particular version of the ACS is used for the folowing reasons:

1. 5-year estimates are the most accurate data outside of the decennial census [as explained here](http://www.census.gov/programs-surveys/acs/guidance/estimates.html).
1. 2013 is the most recent data set with 5-year estimates
1. TIGER/Line® gives you the geographic boundaries of the zip codes so you can perform spatial analyses
1. This data set is smaller than the full Census, but still has the important income, education, race, age and occupation demographics we want to use.

If you want to do this yourself, [this article](https://developer.ibm.com/clouddataservices/2015/09/08/census-open-data-on-ibm-cloud/) explains how to get a CSV out of that format.

### Accessing Census files

Access the files mentioned here via the [IBM Data Science Experience Community](https://apsportal.ibm.com/community). You can get your free, individual "API key" on each data set's detail page:
 
- [Zip code areas](https://console.ng.bluemix.net/data/exchange/public/e/united-states-demographic-measures-land)
- [Age](https://console.ng.bluemix.net/data/exchange/public/e/united-states-demographic-measures-age)
- [Housing](https://console.ng.bluemix.net/data/exchange/public/e/united-states-demographic-measures-housing)

After getting your API key (your personal URL for the data file), in this script replace, for example, `os.environ['AE_KEY_AGE']` with your URL for the Age data CSV file.


### Get zip code areas from Census

In [2]:
AREAS_URL = "https://openobjectstore.mybluemix.net/censusacs2013zip/areas.csv"
geo_df = pd.read_csv( AREAS_URL, usecols=['GEOID_Data','ALAND10'], dtype={"GEOID_Data": np.str, "ALAND10": np.int} )
geo_df.columns = ['ALAND10','GEOID']
geo_df = geo_df.set_index('GEOID')
geo_df.head()

ALAND10
GEOID                  
86000US43451   63411475
86000US43452  121783680
86000US43456    9389360
86000US43457   48035540
86000US43458    2573816

### Get population from Census

In [3]:
POP_URL = "https://apsportal.ibm.com/exchange-api/v1/entries/beb8c30a3f559e58716d983671b65c10/data?accessKey=afb441da02fb0f7f9dcfad44ec5d4b22	"
pop_df = pd.read_csv( POP_URL, usecols=['GEOID','B01001e1'], dtype={"GEOID": np.str} )
pop_df.columns = ['GEOID','POPULATION']
pop_df = pop_df.set_index('GEOID')
pop_df.head()

POPULATION
GEOID                   
86000US01001       17245
86000US01002       29266
86000US01003       11032
86000US01005        5356
86000US01007       14673

### Get housing age from Census
NOTE: this is a large 210Mb file and may take a few minutes to load

In [4]:
HOUSE_URL = "https://openobjectstore.mybluemix.net/censusacs2013zip/x25_housing.csv"
housing_df = pd.read_csv( HOUSE_URL, usecols=['GEOID','B25035e1'], dtype={"GEOID": np.str} )
housing_df = housing_df.set_index('GEOID')
housing_df.sample(5)

B25035e1
GEOID                 
86000US39094    1982.0
86000US04952    1982.0
86000US40202    1967.0
86000US40356    1989.0
86000US55601    1981.0

### Join Census data into one DataFrame with nice names

In [5]:
urban_df = geo_df.join(pop_df)
urban_df = urban_df.join(housing_df)
urban_df.sample(5)

ALAND10  POPULATION  B25035e1
GEOID                                        
86000US21840   13555317         466    1960.0
86000US32408   27351027       16244    1990.0
86000US65566   13104201         819    1974.0
86000US70652  259298584        2219    1989.0
86000US84665   58458879         456    1952.0

In [6]:
urban_df.columns = ['AREAMSQ','Population','MEDYRBUILT']
urban_df.sample(5)

AREAMSQ  Population  MEDYRBUILT
GEOID                                          
86000US56278  333280150        2876      1960.0
86000US07840   90543751       29527      1979.0
86000US44828     564579          23         NaN
86000US23022   67695111        1418      1976.0
86000US47930   66442039        1021      1952.0

## Density calculation

- persons per square km = persons / (area in square meters / 1,000,000)
- persons per hectare = persons / (area in square meters / 10,000)

### Compute population density as persons per square kilometer

In [7]:
urban_df['POPPERKMSQ'] = urban_df['Population'] / (urban_df['AREAMSQ']/1000000)
urban_df.sample(4)

AREAMSQ  Population  MEDYRBUILT   POPPERKMSQ
GEOID                                                       
86000US16651  109915498        6003      1957.0    54.614682
86000US05261   83109539        2835      1974.0    34.111608
86000US63117    6101989        9221      1939.0  1511.146611
86000US40737   18722271        1377      1990.0    73.548770

### Group population density into 4 categories

In [8]:
urban_df['CAT'] = 'EXURBAN'
urban_df['CAT'][(urban_df['POPPERKMSQ'] >= 2900)] = 'URBAN'
urban_df['CAT'][(urban_df['POPPERKMSQ'] < 2900) & (urban_df['POPPERKMSQ'] >= 100) & (urban_df['MEDYRBUILT'] < 1980) & (urban_df['MEDYRBUILT'] >= 1946)] = 'SUBURBANEARLY'
urban_df['CAT'][(urban_df['POPPERKMSQ'] < 2900) & (urban_df['POPPERKMSQ'] >= 100) & (urban_df['MEDYRBUILT'] >= 1980)] = 'SUBURBANLATE'
urban_df.describe()

/Users/rajrsingh/anaconda/lib/python2.7/site-packages/ipykernel/__main__.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  from ipykernel import kernelapp as app
/Users/rajrsingh/anaconda/lib/python2.7/site-packages/ipykernel/__main__.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  app.launch_new_instance()
/Users/rajrsingh/anaconda/lib/python2.7/site-packages/ipykernel/__main__.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy


AREAMSQ     Population    MEDYRBUILT    POPPERKMSQ
count  3.298900e+04   32989.000000  32045.000000  32989.000000
mean   2.250019e+08    9443.177453   1971.068529    487.703913
std    6.575933e+08   13858.010530     15.606758   1912.093435
min    5.094000e+03       0.000000   1939.000000      0.000000
25%    2.351832e+07     719.000000   1961.000000      7.754449
50%    9.322068e+07    2781.000000   1974.000000     30.194351
75%    2.304373e+08   12830.000000   1982.000000    249.247358
max    3.478591e+10  114734.000000   2011.000000  71226.281507

In [9]:
# look at a few records to do a quick sanity check
urban_df.sample(30)

AREAMSQ  Population  MEDYRBUILT   POPPERKMSQ            CAT
GEOID                                                                       
86000US73544   333896814         242      1949.0     0.724775        EXURBAN
86000US01097     4426152          83      1939.0    18.752180        EXURBAN
86000US29817   278653752        5640      1980.0    20.240172        EXURBAN
86000US73009   206537750        1243      1973.0     6.018270        EXURBAN
86000US68845   288926595       21039      1980.0    72.817803        EXURBAN
86000US40923    10421377        1037      1982.0    99.507004        EXURBAN
86000US71859    55922908         466      1980.0     8.332900        EXURBAN
86000US56118   136542873         452      1942.0     3.310316        EXURBAN
86000US74132    31542561        8128      1984.0   257.683579   SUBURBANLATE
86000US50611    78763743         400      1939.0     5.078479        EXURBAN
86000US50171   279967334        2943      1974.0    10.511941        EXURBAN
86000US50648   223049940        4513      1961.0    20.233137        EXURBAN
86000US36260    70314600        3920      1981.0    55.749446        EXURBAN
86000US59521   763283493        3945      1975.0     5.168460        EXURBAN
86000US92880    63949216       66353      2003.0  1037.588952   SUBURBANLATE
86000US71417   359627748        4717      1977.0    13.116341        EXURBAN
86000US58040   208970387         873      1975.0     4.177625        EXURBAN
86000US62244   129288121        1300      1983.0    10.055061        EXURBAN
86000US52349   379632679        7350      1962.0    19.360820        EXURBAN
86000US37309    98350718        2026      1986.0    20.599748        EXURBAN
86000US64427   158792281         672      1947.0     4.231944        EXURBAN
86000US62974    69217524        1364      1980.0    19.705992        EXURBAN
86000US22079    75730897       32986      1993.0   435.568590   SUBURBANLATE
86000US57722  1239063547         491      1939.0     0.396267        EXURBAN
86000US26285    27698192         223      1939.0     8.051067        EXURBAN
86000US50861   112876686         324      1952.0     2.870389        EXURBAN
86000US04454   128052446          57      1962.0     0.445130        EXURBAN
86000US47247      304373          87      1964.0   285.833500  SUBURBANEARLY
86000US70163       10072           0         NaN     0.000000        EXURBAN
86000US63445   429920202        3675      1970.0     8.548098        EXURBAN

## Mapping Urbanity

In [10]:
json_data_from_python = urban_df.reset_index().to_json(orient="records")

In [11]:
from IPython.display import Javascript
#Create a javascript variable called 'vizObj' with our json data to visualize in the browser
#The data object 'vizObj' will be a global varialbe in our window that
#We can pass to another javascript function call
Javascript("""window.vizObj={};""".format(json_data_from_python))

<IPython.core.display.Javascript object>

In [12]:
#Create some HTML to style out map and define it's output size
from IPython.display import HTML
HTML('''
    body{margin:0;padding:0;}#map{position:relative;top:0;bottom:0;width:100%;height:400px;}
''')

In [13]:
%%javascript
require.config({
  paths: {
      mapboxgl: 'https://api.tiles.mapbox.com/mapbox-gl-js/v0.39.1/mapbox-gl',
      bootstrap: 'https://maxcdn.bootstrapcdn.com/bootstrap/3.3.6/js/bootstrap.min'
  }
});

IPython.OutputArea.auto_scroll_threshold = 9999;
require(['mapboxgl', 'bootstrap'], function(mapboxgl, bootstrap){
    mapboxgl.accessToken = 'pk.eyJ1IjoicmFqcnNpbmdoIiwiYSI6ImpzeDhXbk0ifQ.VeSXCxcobmgfLgJAnsK3nw';
    var map = new mapboxgl.Map({
        container: 'map', // HTML element id in which to draw the map
        style: 'mapbox://styles/mapbox/light-v9', //mapbox map to use
        center: [-71.09, 42.44], // starting center position
        zoom: 9 // starting zoom
    });
    
    var densitytypes = ["URBAN", "SUBURBANEARLY", "SUBURBANLATE", "EXURBAN"];
    var densitycolors = ["#d7301f", "#fc8d59", "#fdcc8a", "#fef0d9"];
    
    // Join local JSON data with vector tile geometry
    var maxValue = 71227;
    var data = vizObj;

    // Get the vector geometries to join
    // US Census Data Source
    // https://www.census.gov/geo/maps-data/data/cbf/cbf_state.html
    var mapId = "rajrsingh.bjb1ffhz";
    var layerName = "zipsimple0025-btzfjd";
    var vtMatchProp = "GEOID_Data";
    var dataMatchProp = "GEOID";
    var dataStyleProp = "CAT";


    map.on('load', function() {

        // Add source for state polygons hosted on Mapbox
        map.addSource("zips", {
            type: "vector",
            url: "mapbox://" + mapId
        });

        // First value is the default, used where there is no data
        var stops = [["0", "#888888"]];

        // Calculate color for each state based on the unemployment rate
        data.forEach(function(row) {
            if (densitytypes.indexOf(row[dataStyleProp]) >= 0 ) {
                var color = densitycolors[densitytypes.indexOf(row[dataStyleProp])];
                stops.push([row[dataMatchProp], color]);
            }
        });

        // Add layer from the vector tile source with data-driven style
        map.addLayer({
            "id": "zips-join",
            "type": "fill",
            "source": "zips",
            "source-layer": layerName,
            "paint": {
                "fill-color": {
                    "property": vtMatchProp,
                    "type": "categorical",
                    "stops": stops
                }, 
                "fill-antialias": true, 
                "fill-outline-color": "rgba(255, 255, 255, 0.10)"
            }
        }, 'waterway-label');
    });
});

element.append('<div id="map" style="position:relative;top:0;bottom:0;width:100%;height:400px;"></div>');

<IPython.core.display.Javascript object>